<h1> How to save Gotham </h1>

<h3> Environment </h3>
Create a environment
<ul>
    <li> State Space</li>
    <li> Action space</li>
    <li> Reward functions</li>
    <li>Constraints</li>
    <li> Reset and step functions</li>
</ul>

<h3> Agent </h3>
Create one or mulitple agents to interact with the enivornment
<ul>
    <li>Policy based methods: PPO, DDP, A2C</li>
    <li>Not value based-methods: DQN</li>
    <li> Not actor critic mehods: Involves value-based methods</li>
    <li>Exploration strategy: maybe epislon greedy or Thompson sampling</li>
    <li> The trade-off between explorationa and exploitation happens here.</li>
</ul>

<h3> Training Loop </h3>
Simulation area for agent to interact in environment
<ul>
    <li>Collect state, action and reward</li>
    <li>Update policy and/or network using gradient based optimization</li>
    <li>Apply techniques like eperience replay and target networks</li>
    <!-- <li></li> -->
</ul>

<h3>Evaluation</h3>
Assess performance of agent
<ul>
    <li>Out-of-sample testing</li>
    <li> Performance measurement</li>
    <li> Attribution analysis</li>
    <!-- <li></li> -->
</ul>


<h3> Hyperparameter tuning and optimization</h3>

<ul>
    <li>Fine tune using: grid search, random search and bayesian optimization</li>
    <!-- <li></li>
    <li></li>
    <li></li> -->
</ul>


<h3>Saving and Loading Model</h3>
Ensure reproduability
<ul>
    <li> Save model</li>
    <!-- <li></li>
    <li></li>
    <li></li> -->
</ul>


In [1]:
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt

import yfinance as yf

from scipy.optimize import Bounds
from scipy.optimize import LinearConstraint
from scipy.optimize import minimize

import gymnasium as gym
from gymnasium import spaces

from stable_baselines3 import PPO
from stable_baselines3.common.env_checker import check_env

import torch as th
from torch import nn, optim

from Data_Retriever import DataRetriever as DatRet
from Markowitz_PT import MarkowitzPT as MPT
from Menchero_OGA import MencheroOGA as MOGA

In [2]:
# Defining stock pool
ticker_df =  pd.DataFrame()
ticker_df["Petroleum"] = ["EQNR.OL", "AKRBP.OL", "SUBC.OL", "BWO.OL",]
ticker_df["Seafood (food)"] = ["ORK.OL", "MOWI.OL", "SALM.OL", "LSG.OL"]
ticker_df["Technologies"] = ["TEL.OL", "NOD.OL", "ATEA.OL", "BOUV.OL"]
ticker_df["Financial"] = ["STB.OL", "DNB.OL", "GJF.OL", "AKER.OL"]
ticker_df["Shipping"] = ["WAWI.OL", "SNI.OL", "BELCO.OL", "ODF.OL"]
ticker_df

# Defining ESG scores for respective securities
esg_scores = [36.6, 35.3, 17.9, 18, 
              18, 21.2, 18.7, 
              19.8, 13.8, 18.1, 19, 
              17.2, 14, 17.2, 19.5, 
              19.7, 21.2, 26.8, 19.3]

In [3]:
# Retrieve data from yf API: y-m-d
data = DatRet(ticker_df, "2020-01-01", "2024-01-01")

# In function below, set log=True to check for data availability
data.retrieve_data()

YF.download() has changed argument auto_adjust default to True


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed

1 Failed download:
['LSG.OL']: YFPricesMissingError('possibly delisted; no price data found  (1d 2020-01-01 -> 2024-01-01)')
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%********************

'--Data retrieved successfully--'

In [4]:
return_array =  [pd.Series(stock) for sector in data.raw_data for stock in sector]
return_df = pd.DataFrame(return_array)
return_tdf = return_df.T

In [5]:
df = return_tdf.drop(7, axis=1)

<h1>---------------------------------------------</h1>
<h2> Environment </h2>

<h2> PPO agent </h2>

In [6]:
from sklearn.model_selection import train_test_split

from RL_Algorithm.ThesisEnvironment  import PortfolioEnvironment as PorEnv
from RL_Algorithm.ThesisModel import LSTMPolicy as PolMod
from RL_Algorithm.ThesisModel import train_agent, test_agent

In [7]:
stock_data = df
esg_data = esg_scores

In [8]:
from sklearn.model_selection import train_test_split

# Assuming your stock_data and esg_data are numpy arrays
stock_data_train, stock_data_test= train_test_split(
    stock_data, test_size=0.2, shuffle=False
)

# Create training and testing environments
train_env = PorEnv(stock_data_train, esg_data, max_steps=50)
test_env = PorEnv(stock_data_test, esg_data, max_steps=50)

# Train the model on the training environment
trained_model = train_agent(train_env, learning_rate=0.001, episodes=50)

# Test the agent
test_agent(test_env, trained_model)


Episode 0 - Total Reward: 124.79314502444589
Episode 10 - Total Reward: 124.79314502444589
Episode 20 - Total Reward: 124.79314502444589
Episode 30 - Total Reward: 124.79314502444589
Episode 40 - Total Reward: 124.79314502444589
Total Test Reward: 21.508720936324277


[OrderedDict([('lstm.weight_ih_l0',
               tensor([[-0.0242,  0.0312,  0.0643,  ..., -0.0668, -0.0439,  0.0039],
                       [ 0.0028,  0.0135,  0.0551,  ...,  0.0613,  0.0826, -0.0006],
                       [-0.0528, -0.0696,  0.0610,  ..., -0.0121,  0.0347,  0.0753],
                       ...,
                       [-0.0604,  0.0493, -0.0571,  ...,  0.0238, -0.0522,  0.0063],
                       [-0.0187, -0.0129,  0.0110,  ...,  0.0392, -0.0801, -0.0632],
                       [ 0.0883, -0.0235, -0.0233,  ...,  0.0419, -0.0598,  0.0218]])),
              ('lstm.weight_hh_l0',
               tensor([[-0.0721,  0.0283,  0.0746,  ...,  0.0338, -0.0686,  0.0460],
                       [-0.0082,  0.0190, -0.0807,  ..., -0.0562, -0.0578, -0.0413],
                       [-0.0042,  0.0601,  0.0350,  ...,  0.0091,  0.0004, -0.0343],
                       ...,
                       [ 0.0578,  0.0290, -0.0351,  ...,  0.0411,  0.0862,  0.0585],
                   